<a href="https://colab.research.google.com/github/Ankitha2003/medical-chatbot/blob/main/Copy_of_medical_chatbot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Required Libraries

In [ ]:
pip install transformers

In [ ]:
import torch
torch.__version__

'2.4.0+cu121'

# Install torch-scatter

In [ ]:
!pip install torch-scatter -f https://pytorch-geometric.com/whl/torch-2.4.0+cu121.html

Looking in links: https://pytorch-geometric.com/whl/torch-2.4.0+cu121.html


# Import Libraries

In [ ]:
from transformers import pipeline
import pandas as pd

# Initialize TAPAS Pipeline

In [ ]:
tqa = pipeline(task="table-question-answering",model="google/tapas-base-finetuned-wtq")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
TAPAS models are not usable since `tensorflow_probability` can't be loaded. It seems you have `tensorflow_probability` installed with the wrong tensorflow version. Please try to reinstall it following the instructions here: https://github.com/tensorflow/probability.


In [ ]:
import json

In [ ]:
file_path = 'Guide_Lines.jsonl'


# Load Data from JSONL File

In [ ]:
with open(file_path, 'r') as file:
    data = [json.loads(line) for line in file]

# Load Data into DataFrame

In [ ]:
file_path = 'Guide_Lines.jsonl'
df = pd.read_json(file_path, lines=True)

In [ ]:
pip install datasets

# Import load_dataset from datasets

In [ ]:
from datasets import load_dataset

In [ ]:
dataset = load_dataset('json', data_files='Guide_Lines.jsonl')

# Mount Google Drive

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# Now you can access your JSONL file like this:
file_path = 'Guide_Lines.jsonl'

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Load and Display First Entry from JSONL File

In [ ]:
import json

file_path = 'Guide_Lines.jsonl'

with open(file_path, 'r') as file:
    data = [json.loads(line) for line in file]

# Display the first entry
print(data[0])

{'id': '6', 'text': ' Title: Treatment of Drug-Resistant Tuberculosis. An Official ATS/CDC/ERS/IDSA Clinical Practice Guideline, Update Status: An update to this guideline is in development (est. publication 12/2023), combined with an update to the Drug-Susceptible Tuberculosis guideline. This update will be a joint effort with the American Thoracic Society (ATS), the Centers for Disease Control and Prevention, the European Respiratory Society, and IDSA; the guideline update will be overseen by ATS.,Abstract: BackgroundThe American Thoracic Society, U.S. Centers for Disease Control and Prevention, European Respiratory Society, and Infectious Diseases Society of America jointly sponsored this new practice guideline on the treatment of drug-resistant tuberculosis (DR-TB). The document includes recommendations on the treatment of multidrug-resistant TB (MDR-TB) as well as isoniazid-resistant but rifampin-susceptible TB.MethodsPublished systematic reviews, meta-analyses, and a new individu

# Process Data from JSONL File

In [ ]:
import json

# Load the JSONL file into a list of dictionaries
file_path = 'Guide_Lines.jsonl'

with open(file_path, 'r') as file:
    data = [json.loads(line) for line in file]
processed_data = []

for entry in data:
    processed_data.append({
        'id': entry['id'],
        'text': entry['text'],
        'source': entry['source'],
        'metadata': entry['metadata']
    })

In [ ]:
def find_relevant_entry(query, data):
    results = []
    query = query.lower()
    for entry in data:
        if query in entry['text'].lower():
            results.append(entry)
    return results

In [ ]:
print(processed_data[:3])

[{'id': '6', 'text': ' Title: Treatment of Drug-Resistant Tuberculosis. An Official ATS/CDC/ERS/IDSA Clinical Practice Guideline, Update Status: An update to this guideline is in development (est. publication 12/2023), combined with an update to the Drug-Susceptible Tuberculosis guideline. This update will be a joint effort with the American Thoracic Society (ATS), the Centers for Disease Control and Prevention, the European Respiratory Society, and IDSA; the guideline update will be overseen by ATS.,Abstract: BackgroundThe American Thoracic Society, U.S. Centers for Disease Control and Prevention, European Respiratory Society, and Infectious Diseases Society of America jointly sponsored this new practice guideline on the treatment of drug-resistant tuberculosis (DR-TB). The document includes recommendations on the treatment of multidrug-resistant TB (MDR-TB) as well as isoniazid-resistant but rifampin-susceptible TB.MethodsPublished systematic reviews, meta-analyses, and a new individ

# Install fuzzywuzzy with Speedup

In [ ]:
!pip install fuzzywuzzy[speedup]

In [ ]:
from fuzzywuzzy import process


# Update Function to Find Relevant Entries with Text Preprocessing

In [ ]:
import re

def find_relevant_entry(query, data):
    query = query.lower()
    results = []

    # Clean and preprocess the query
    query_words = set(re.findall(r'\w+', query))

    for entry in data:
        entry_text = entry['text'].lower()
        # Check if any query word is present in the entry text
        if any(word in entry_text for word in query_words):
            results.append(entry)

    return results


In [ ]:
# Example query for testing
test_query = "What are the guidelines for the treatment of drug-resistant tuberculosis?"
results = find_relevant_entry(test_query, processed_data)
print(results)


[{'id': '6', 'text': ' Title: Treatment of Drug-Resistant Tuberculosis. An Official ATS/CDC/ERS/IDSA Clinical Practice Guideline, Update Status: An update to this guideline is in development (est. publication 12/2023), combined with an update to the Drug-Susceptible Tuberculosis guideline. This update will be a joint effort with the American Thoracic Society (ATS), the Centers for Disease Control and Prevention, the European Respiratory Society, and IDSA; the guideline update will be overseen by ATS.,Abstract: BackgroundThe American Thoracic Society, U.S. Centers for Disease Control and Prevention, European Respiratory Society, and Infectious Diseases Society of America jointly sponsored this new practice guideline on the treatment of drug-resistant tuberculosis (DR-TB). The document includes recommendations on the treatment of multidrug-resistant TB (MDR-TB) as well as isoniazid-resistant but rifampin-susceptible TB.MethodsPublished systematic reviews, meta-analyses, and a new individ

# Add Debugging to Relevant Entry Search Function

In [ ]:
def find_relevant_entry(query, data):
    query = query.lower()
    results = []

    print(f"Processing query: {query}")  # Debug print
    query_words = set(re.findall(r'\w+', query))
    print(f"Query words: {query_words}")  # Debug print

    for entry in data:
        entry_text = entry['text'].lower()
        print(f"Checking entry: {entry_text[:100]}...")  # Debug print (first 100 chars)

        if any(word in entry_text for word in query_words):
            results.append(entry)

    return results


In [ ]:
for entry in processed_data:
    if 'drug-resistant tuberculosis' in entry['text'].lower():
        print(entry)


{'id': '6', 'text': ' Title: Treatment of Drug-Resistant Tuberculosis. An Official ATS/CDC/ERS/IDSA Clinical Practice Guideline, Update Status: An update to this guideline is in development (est. publication 12/2023), combined with an update to the Drug-Susceptible Tuberculosis guideline. This update will be a joint effort with the American Thoracic Society (ATS), the Centers for Disease Control and Prevention, the European Respiratory Society, and IDSA; the guideline update will be overseen by ATS.,Abstract: BackgroundThe American Thoracic Society, U.S. Centers for Disease Control and Prevention, European Respiratory Society, and Infectious Diseases Society of America jointly sponsored this new practice guideline on the treatment of drug-resistant tuberculosis (DR-TB). The document includes recommendations on the treatment of multidrug-resistant TB (MDR-TB) as well as isoniazid-resistant but rifampin-susceptible TB.MethodsPublished systematic reviews, meta-analyses, and a new individu

# Define and Run Medical Guidelines Chatbot

In [ ]:
def chatbot():
    print("Welcome to the Medical Guidelines Chatbot!")
    print("Ask me about drug-resistant tuberculosis treatment guidelines.")
    print("Type 'exit' to end the conversation.")

    while True:
        try:
            query = input("\nYou: ")
            if query.lower() == 'exit':
                print("Goodbye!")
                break

            # Debugging: Print the query to ensure it's being captured
            print(f"Debug: User query received - {query}")

            results = find_relevant_entry(query, processed_data)

            if results:
                # Limit the number of results displayed to 3 to 5 lines
                max_results_to_display = 3
                display_count = min(max_results_to_display, len(results))
                print(f"\nBot: Here are the top {display_count} entries related to your query:")
                for i in range(display_count):
                    result = results[i]
                    print(f"\nSource: {result['source']}")
                    print(f"Text: {result['text'][:100]}...")  # Show only the first 300 characters of the text
            else:
                print("Bot: Sorry, I couldn't find anything related to your query.")
        except Exception as e:
            print(f"An error occurred: {e}")

# Run the chatbot
chatbot()


Welcome to the Medical Guidelines Chatbot!
Ask me about drug-resistant tuberculosis treatment guidelines.
Type 'exit' to end the conversation.

You: What are the recommended treatments for drug-resistant tuberculosis?
Debug: User query received - What are the recommended treatments for drug-resistant tuberculosis?
Processing query: what are the recommended treatments for drug-resistant tuberculosis?
Query words: {'what', 'recommended', 'the', 'treatments', 'are', 'resistant', 'tuberculosis', 'drug', 'for'}
Checking entry:  title: treatment of drug-resistant tuberculosis. an official ats/cdc/ers/idsa clinical practice gui...
Checking entry:  title: ats/idsa guidelines for diagnosis and treatment of adults with community-acquired pneumonia,...
Checking entry:  title: ats/idsa 2016 clinical practice guidelines for the management of adults with hospital-acquir...
Checking entry:  title: idsa 2017 clinical practice guidelines for healthcare-associated ventriculitis and meningiti...
Checking